# Visualize Road Edges and Object Trajectories for Collision Checking

In [1]:
import json
import trimesh
import numpy as np

In [2]:
f = open('../data/processed/training/tfrecord-00000-of-01000_3.json', 'r')
scene = json.load(f)

In [3]:
scene.keys()

dict_keys(['name', 'scenario_id', 'objects', 'roads', 'tl_states'])

In [4]:
scene["objects"][0].keys()

dict_keys(['position', 'width', 'length', 'height', 'heading', 'velocity', 'valid', 'goalPosition', 'type', 'mark_as_expert'])

In [5]:
# Meshes for collision checking
def generate_mesh(segments, height=2.0, width=0.2, color=None):
    segments = np.array(segments, dtype=np.float64)
    starts, ends = segments[:, 0, :], segments[:, 1, :]
    directions = ends - starts
    lengths = np.linalg.norm(directions, axis=1, keepdims=True)
    unit_directions = directions / lengths
    
    # Create the base box mesh with the height along the z-axis
    base_box = trimesh.creation.box(extents=[1.0, width, height])
    base_box.apply_translation([0.5, 0, 0])  # Align box's origin to its start
    
    # Prepare rotation matrices around the z-axis
    z_axis = np.array([0, 0, 1])  # The desired vertical axis
    angles = np.arctan2(unit_directions[:, 1], unit_directions[:, 0])  # Rotation in the XY plane

    rectangles = []
    lengths = lengths.flatten()

    for i, (start, length, angle) in enumerate(zip(starts, lengths, angles)):
        # Copy the base box and scale to match segment length
        scaled_box = base_box.copy()
        scaled_box.apply_scale([length, 1.0, 1.0])
        
        # Apply rotation around the z-axis
        rotation_matrix = trimesh.transformations.rotation_matrix(angle, z_axis)
        scaled_box.apply_transform(rotation_matrix)
        
        # Translate the box to the segment's starting point
        scaled_box.apply_translation(start)
        if color is not None:
            scaled_box.visual.face_colors = color
        rectangles.append(scaled_box)

    # Concatenate all boxes into a single mesh
    mesh = trimesh.util.concatenate(rectangles)
    return mesh

In [6]:
# Construct road edges
edge_segments = []
for road in scene['roads']:
    if road["type"] == 'road_edge':
        edge_vertices = [[r["x"], r["y"], r["z"]] for r in road["geometry"]]
        edge_segments += [[edge_vertices[i], edge_vertices[i+1]] for i in range(len(edge_vertices) - 1)]
edge_mesh = generate_mesh(edge_segments)

In [7]:
# Construct objects
object_meshes = []
for object in scene['objects']:
    if object['type'] not in ['vehicle', 'cyclist']:
        continue
    if False in object["valid"]:
        # Create trajectory segments of only valid positions
        trajectory_segments = []
        for i in range(len(object["position"]) - 1):
            if object["valid"][i] and object["valid"][i + 1]:
                trajectory_segments.append([[object["position"][i]["x"], object["position"][i]["y"], object["position"][i]["z"]],
                                            [object["position"][i+1]["x"], object["position"][i+1]["y"], object["position"][i+1]["z"]]])
    else:
        object_vertices = [[pos["x"], pos["y"], pos["z"]] for pos in object["position"]]
        trajectory_segments = [[object_vertices[i], object_vertices[i+1]] for i in range(len(object_vertices) - 1)]
    if len(trajectory_segments) > 0:
        if object["mark_as_expert"] == True: 
            trajectory_mesh = generate_mesh(trajectory_segments, color=(180,0,0,60))
        else:
            trajectory_mesh = generate_mesh(trajectory_segments, color=(0,180,0,60))
        object_meshes.append(trajectory_mesh)

In [8]:
# Render
view = trimesh.Scene()
view.add_geometry(edge_mesh, node_name="Road Edges")
for i, mesh in enumerate(object_meshes):
        view.add_geometry(mesh, node_name=f"Vehicle {i} Path")
view.show()